# Encrypt a Model

Forge Model Encryption is intended to secure your model from the development environment of LEIP Optimize to the deployment environment. We facilitate encrypting the optimized/compiled artifact with a secure key and password. You will only be able to load this artifact at runtime with these credentials.

## Loading the Model into Forge

We will start by selecting a pre-trained model, specifically `microsoft/resnet-50` from Hugging Face exported as an `.onnx` model. You can select any model family support by Forge. However, we recommend models less than 100MB in size, as larger models can take significantly longer to encrypt.

In [ ]:
import os
import onnx
import forge
from optimum.exporters.onnx import main_export

Download the model from Hugging Face.

In [ ]:
model_path = "models"
if not os.path.exists(model_path):
    os.makedirs(model_path)
if not os.path.exists(f"{model_path}/resnet-50/model.onnx"):
    model_id = "microsoft/resnet-50"
    output_dir = f"{model_path}/resnet-50"
    main_export(
        model_name_or_path=model_id,
        output=output_dir,
        task="image-classification",
        no_dynamic_axes=True,
        opset=12,
        device="cpu"
    )

And load the model into Forge.

In [7]:
onnx_model = onnx.load(f"{model_path}/resnet-50/model.onnx")
ir = forge.RelayModule.from_onnx(onnx_model)

## Compile and Encrypt the Model
You can perform Forge graph optimizations and modifications just as you would on an unencrypted model.
Encryption only affects the compilation stage. You call the same API but with an additional parameter: `encrypt_password`. You can then encrypt the compiled output to secure your model from this environment to the runtime target environment.

We will create a directory `compiled_encrypted_outputs` to save our compiled model library. We will also select a target and an output path. Finally, we need to provide a password to signal our intent to encrypt.

In [ ]:
encrypted_output_dir = "encrypted_output"
if not os.path.exists(encrypted_output_dir):
    os.makedirs(encrypted_output_dir)

target = "llvm"
output_path = f"{encrypted_output_dir}"
password = "test_password"

With these configurations, we can then use the `compile` function to also encrypt the produced artifact. It will take more time than compilation alone. With my environment, model, and target, for example, encryption takes 10 minutes.

In [ ]:
ir.compile(
        target=target,
        output_path=output_path,
        force_overwrite=True,
        encrypt_password=password,
    )

## Running the Model

Now that you have successfully created an encrypted model library, you're ready to take this artifact over an unsafe channel to your target. Once there, you can use [LEIP Deploy](https://docs.latentai.io/leip/deploy/latest/content/tutorials/run-encrypted-models/) to unlock and deploy the model on the target.